# Blocking with Word2Vec

In [1]:
from gensim.models import Word2Vec
from gensim.utils import simple_preprocess
from sklearn.cluster import KMeans
import numpy as np
import pandas as pd
import os
import gensim.downloader as api
from sklearn.metrics import silhouette_score
import csv

In [2]:
import os

num_threads = os.cpu_count()
print("Numero di thread disponibili:", num_threads)

Numero di thread disponibili: 8


In [3]:
schema_mediato = pd.read_csv("./../../datasets/MediatedSchemaSemicolon.csv",sep=";")

In [4]:
schema_mediato

name                         location        marketCap sharePrice  \
0       Lacework          United States, San Jose            $8.3B        NaN   
1        Tipalti         United States, San Mateo            $8.3B        NaN   
2         Tempus           United States, Chicago            $8.1B        NaN   
3        Anduril            United States, Irvine           $8.48B        NaN   
4           Bolt                 Estonia, Tallinn            $8.4B        NaN   
...          ...                              ...              ...        ...   
81701    PepsiCo      Purchase, NY, United States  $241.05 Billion        NaN   
81702     Costco      Issaquah, WA, United States  $258.15 Billion        NaN   
81703   Broadcom      San Jose, CA, United States  $265.27 Billion        NaN   
81704  Coca-Cola       Atlanta, GA, United States  $273.20 Billion        NaN   
81705      Lilly  Indianapolis, IN, United States  $273.01 Billion        NaN   

                      category foundationYear  
0                Cybersecurity           2015  
1                      Fintech           2010  
2                       Health           2015  
3      Artificial intelligence           2017  
4        Auto & transportation           2013  
...                        ...            ...  
81701                      NaN            NaN  
81702                      NaN            NaN  
81703                      NaN            NaN  
81704                      NaN            NaN  
81705                      NaN            NaN  

[81706 rows x 6 columns]

In [5]:
records = []

In [6]:
for i in range(0,len(schema_mediato)):
    record = schema_mediato.iloc[i].dropna()
    records.append(record.tolist())

In [7]:
records

[['Lacework', 'United States, San Jose', '$8.3B', 'Cybersecurity', '2015'],
 ['Tipalti', 'United States, San Mateo', '$8.3B', 'Fintech', '2010'],
 ['Tempus', 'United States, Chicago', '$8.1B', 'Health', '2015'],
 ['Anduril',
  'United States, Irvine',
  '$8.48B',
  'Artificial intelligence',
  '2017'],
 ['Bolt', 'Estonia, Tallinn', '$8.4B', 'Auto & transportation', '2013'],
 ['ByteDance', 'China, Beijing', '$140B', 'Artificial intelligence', '2012'],
 ['Niantic',
  'United States, San Francisco',
  '$9B',
  'Mobile & telecommunications',
  '2015'],
 ['OYO Rooms', 'India, Gurugram', '$9B', 'Travel', '2012'],
 ['Kavak',
  'Mexico, Lerma de Villada',
  '$8.7B',
  'E-commerce & direct-to-consumer',
  '2014'],
 ['Personio',
  'Germany, Munich',
  '$8.5B',
  'Internet software & services',
  '2015'],
 ['Klaviyo',
  'United States, Boston',
  '$9.2B',
  'Internet software & services',
  '2012'],
 ['Rapyd', 'United Kingdom, London', '$8.75B', 'Fintech', '2016'],
 ['Nuro',
  'United States, Mou

In [8]:
model = Word2Vec(sentences=records, vector_size=256, window=5, min_count=1, workers=4)

In [9]:
def calculate_vector(record):
    # Inizializza un vettore vuoto
    record_vector = np.zeros(model.vector_size)
    # Somma i vettori di embedding di ciascun token nel record
    for token in record:
        record_vector += model.wv[token]
    #Normalizza il vettore risultante
    record_vector /= 256
    return record_vector

In [10]:
records_w2v = []
for i in range(0, len(records)):
    records_w2v.append(calculate_vector(records[i]))

In [11]:
records_w2v

[array([ 1.82684900e-03, -2.31808220e-03, -1.39841705e-03,  1.25354455e-03,
         3.12164062e-03,  2.27169800e-04,  1.49511352e-03,  1.27961309e-04,
        -1.97635699e-03,  2.19403183e-03,  1.65652045e-04, -1.92865706e-03,
        -1.24160410e-04, -1.52913312e-03, -1.85483904e-03,  7.94690504e-04,
         1.11331174e-03, -1.72165340e-03, -4.10663027e-03,  5.31825066e-03,
         2.01045403e-03,  1.86023918e-03, -5.55551892e-04, -4.14689798e-03,
        -1.61528101e-03,  1.48842268e-03,  1.69819438e-03, -1.15388539e-03,
         9.55033385e-04, -3.33117975e-03, -4.11478056e-04,  1.38972396e-03,
        -5.76004710e-04, -2.70623555e-04, -9.16747261e-04,  8.48888265e-04,
         2.62881986e-03, -2.07964407e-03, -1.17928307e-03, -1.48291304e-03,
        -1.74259074e-03,  2.72098021e-03, -1.78572763e-03,  1.59771440e-03,
         3.31434122e-03, -5.60658180e-04, -1.45815709e-04,  3.65973827e-04,
        -1.40390230e-03, -6.25133138e-04, -6.58929517e-04,  8.08399736e-04,
         7.4

In [12]:
df = pd.DataFrame(records_w2v)
df

0         1         2         3         4         5         6    \
0      0.001827 -0.002318 -0.001398  0.001254  0.003122  0.000227  0.001495   
1      0.003022 -0.003315 -0.001642  0.001770  0.004313  0.000616  0.001876   
2      0.002205 -0.002794 -0.001764  0.001475  0.003747  0.000315  0.001744   
3      0.001792 -0.002004 -0.001086  0.001112  0.002648  0.000296  0.001203   
4      0.001827 -0.002173 -0.001071  0.001228  0.002748  0.000211  0.001340   
...         ...       ...       ...       ...       ...       ...       ...   
81701  0.000204 -0.000186 -0.000002  0.000108  0.000203  0.000042  0.000091   
81702  0.000073 -0.000058 -0.000007  0.000027  0.000059  0.000034  0.000027   
81703  0.000441 -0.000403 -0.000075  0.000253  0.000468  0.000070  0.000188   
81704  0.000416 -0.000389 -0.000045  0.000268  0.000448  0.000063  0.000191   
81705  0.000071 -0.000068 -0.000027  0.000051  0.000099  0.000025  0.000035   

            7         8         9    ...       246       247       248  \
0      0.000128 -0.001976  0.002194  ...  0.000124  0.001602  0.001369   
1      0.000342 -0.002306  0.002305  ...  0.000862  0.002248  0.001649   
2      0.000110 -0.002464  0.002731  ... -0.000033  0.001901  0.001718   
3      0.000177 -0.001465  0.001500  ...  0.000431  0.001344  0.001066   
4      0.000182 -0.001601  0.001730  ...  0.000324  0.001452  0.001132   
...         ...       ...       ...  ...       ...       ...       ...   
81701  0.000054 -0.000050  0.000019  ...  0.000179  0.000106  0.000053   
81702  0.000034 -0.000002  0.000037  ...  0.000053  0.000042 -0.000016   
81703  0.000095 -0.000090  0.000035  ...  0.000302  0.000265  0.000098   
81704  0.000077 -0.000118  0.000057  ...  0.000301  0.000259  0.000075   
81705  0.000041 -0.000039 -0.000019  ...  0.000054  0.000049  0.000021   

            249       250       251       252       253       254       255  
0     -0.001499 -0.002055 -0.000260 -0.003131  0.002729 -0.002839  0.000488  
1     -0.001982 -0.002540 -0.000485 -0.003931  0.003246 -0.003682  0.000618  
2     -0.001869 -0.002592 -0.000316 -0.003930  0.003434 -0.003426  0.000646  
3     -0.001234 -0.001606 -0.000221 -0.002487  0.002109 -0.002249  0.000434  
4     -0.001273 -0.001738 -0.000206 -0.002703  0.002236 -0.002482  0.000339  
...         ...       ...       ...       ...       ...       ...       ...  
81701 -0.000089 -0.000089 -0.000029 -0.000119  0.000073 -0.000137  0.000036  
81702 -0.000014 -0.000027 -0.000006 -0.000022  0.000045 -0.000046  0.000015  
81703 -0.000138 -0.000193 -0.000073 -0.000277  0.000164 -0.000364  0.000036  
81704 -0.000171 -0.000160 -0.000062 -0.000259  0.000153 -0.000345  0.000037  
81705 -0.000020 -0.000023 -0.000020 -0.000069  0.000068 -0.000037  0.000008  

[81706 rows x 256 columns]

## K Means

In [13]:
kmeans = KMeans(n_clusters=2167, random_state=0).fit(df)

/Users/alessandropesare/anaconda3/envs/FinalProjectIDD3_8/lib/python3.8/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


In [14]:
len(kmeans.labels_)

81706

In [15]:
kmeans.labels_

array([ 110,  263,  578, ...,   90, 1158, 1590], dtype=int32)

In [16]:
schema_mediato['block'] = kmeans.labels_

In [17]:
schema_mediato

name                         location        marketCap sharePrice  \
0       Lacework          United States, San Jose            $8.3B        NaN   
1        Tipalti         United States, San Mateo            $8.3B        NaN   
2         Tempus           United States, Chicago            $8.1B        NaN   
3        Anduril            United States, Irvine           $8.48B        NaN   
4           Bolt                 Estonia, Tallinn            $8.4B        NaN   
...          ...                              ...              ...        ...   
81701    PepsiCo      Purchase, NY, United States  $241.05 Billion        NaN   
81702     Costco      Issaquah, WA, United States  $258.15 Billion        NaN   
81703   Broadcom      San Jose, CA, United States  $265.27 Billion        NaN   
81704  Coca-Cola       Atlanta, GA, United States  $273.20 Billion        NaN   
81705      Lilly  Indianapolis, IN, United States  $273.01 Billion        NaN   

                      category foundationYear  block  
0                Cybersecurity           2015    110  
1                      Fintech           2010    263  
2                       Health           2015    578  
3      Artificial intelligence           2017    678  
4        Auto & transportation           2013    244  
...                        ...            ...    ...  
81701                      NaN            NaN      0  
81702                      NaN            NaN   2133  
81703                      NaN            NaN     90  
81704                      NaN            NaN   1158  
81705                      NaN            NaN   1590  

[81706 rows x 7 columns]

In [18]:
schema_mediato.to_csv("SchemaMediatoConCluster.csv")

In [68]:
silhouette_score(df,kmeans.labels_)

0.2472871892915824

In [39]:
from itertools import islice

In [40]:

#Esegui il blocking basato sui cluster ottenuti
blocks = {}  # Dizionario che mappa il cluster al suo insieme di record
for i, label in enumerate(kmeans.labels_):
    if label not in blocks:
        blocks[label] = []
    blocks[label].append(records[i])

print("Blocchi ottenuti:")
print(len(blocks))
# Stampare i primi 100 elementi del dizionario
for key, value in islice(blocks.items(), 100):
    print(key, value)

Blocchi ottenuti:
800
403 [['Lacework', 'United States, San Jose', '$8.3B', 'Cybersecurity', '2015'], ['Nuro', 'United States, Mountain View', '$8.6B', 'Auto & transportation', '2016'], ['Lalamove', 'Hong Kong, Cheung Sha Wan', '$10B', 'Supply chain, logistics, & delivery', '2013'], ['Leap Motor', 'China, Hangzhou', '$1.01B', 'Auto & transportation', '2015'], ['Rivigo', 'India, Gurgaon', '$1.07B', 'Supply chain, logistics, & delivery', '2014'], ['LEAD School', 'India, Andheri', '$1.1B', 'Edtech', '2012'], ['Flexe', 'United States, Seattle', ' $1B', 'Supply chain, logistics, & delivery', '2013'], ['TravelPerk', 'Spain, Barcelona', '$1.3B', 'Travel', '2015'], ['Tongdun Technology', 'China, Hangzhou', '$1.32B', 'Cybersecurity', '2013'], ['Degreed', 'United States, Pleasanton', '$1.4B', 'Edtech', '2012'], ['Fresh Life Style Supply Chain Management', 'China, Chengdu', ' $1.57 B', 'Supply chain, logistics, & delivery', '2016'], ['Ximalaya FM', 'China, Shanghai', '$1.52B', 'Mobile & telecommu

In [44]:
blocks[403]

[['Lacework', 'United States, San Jose', '$8.3B', 'Cybersecurity', '2015'],
 ['Nuro',
  'United States, Mountain View',
  '$8.6B',
  'Auto & transportation',
  '2016'],
 ['Lalamove',
  'Hong Kong, Cheung Sha Wan',
  '$10B',
  'Supply chain, logistics, & delivery',
  '2013'],
 ['Leap Motor', 'China, Hangzhou', '$1.01B', 'Auto & transportation', '2015'],
 ['Rivigo',
  'India, Gurgaon',
  '$1.07B',
  'Supply chain, logistics, & delivery',
  '2014'],
 ['LEAD School', 'India, Andheri', '$1.1B', 'Edtech', '2012'],
 ['Flexe',
  'United States, Seattle',
  ' $1B',
  'Supply chain, logistics, & delivery',
  '2013'],
 ['TravelPerk', 'Spain, Barcelona', '$1.3B', 'Travel', '2015'],
 ['Tongdun Technology', 'China, Hangzhou', '$1.32B', 'Cybersecurity', '2013'],
 ['Degreed', 'United States, Pleasanton', '$1.4B', 'Edtech', '2012'],
 ['Fresh Life Style Supply Chain Management',
  'China, Chengdu',
  ' $1.57 B',
  'Supply chain, logistics, & delivery',
  '2016'],
 ['Ximalaya FM',
  'China, Shanghai',
  

## Preparazione per Record Linkage

In [45]:
schema_con_cluster = schema_mediato.copy()
schema_con_cluster['block'] = kmeans.labels_

In [46]:
schema_con_cluster

name                         location        marketCap sharePrice  \
0       Lacework          United States, San Jose            $8.3B        NaN   
1        Tipalti         United States, San Mateo            $8.3B        NaN   
2         Tempus           United States, Chicago            $8.1B        NaN   
3        Anduril            United States, Irvine           $8.48B        NaN   
4           Bolt                 Estonia, Tallinn            $8.4B        NaN   
...          ...                              ...              ...        ...   
81701    PepsiCo      Purchase, NY, United States  $241.05 Billion        NaN   
81702     Costco      Issaquah, WA, United States  $258.15 Billion        NaN   
81703   Broadcom      San Jose, CA, United States  $265.27 Billion        NaN   
81704  Coca-Cola       Atlanta, GA, United States  $273.20 Billion        NaN   
81705      Lilly  Indianapolis, IN, United States  $273.01 Billion        NaN   

                      category foundationYear  cluster  
0                Cybersecurity           2015      403  
1                      Fintech           2010      610  
2                       Health           2015      687  
3      Artificial intelligence           2017      372  
4        Auto & transportation           2013      372  
...                        ...            ...      ...  
81701                      NaN            NaN      328  
81702                      NaN            NaN      328  
81703                      NaN            NaN      678  
81704                      NaN            NaN      678  
81705                      NaN            NaN        8  

[81706 rows x 7 columns]

In [47]:
schema_con_cluster.to_csv("SchemaMediatoConCluster.csv")

## Esempio per un solo cluster

In [23]:
cluster5 = schema_con_cluster[schema_con_cluster['cluster'] == 5]
cluster5

name  \
10123                       ValueLabs   
10172                      Tata Elxsi   
10331      Sysnet Global Technologies   
10592  Barclays Global Service Centre   
10843  SoftAge Information Technology   
11220    PrimEra Medical Technologies   
11322     National Informatics Centre   
11344                       Suma Soft   
11556                          Sasken   
11568                IIC Technologies   
11811                    SG Analytics   
11962         Ensure Support Services   
12039                          RedBus   
12893              Bharat IT Services   
12896             e-Centric Solutions   
13035           Uneecops Technologies   
13167             Atyati Technologies   
14080              Syscom Corporation   
14095              Syscom Corporation   
14113                 Webkul Software   
14391                    Innovatiview   
14536                     InnovationM   
14681              Tudip Technologies   
14713              Tudip Technologies   
14838                  Aapna Infotech   
16077                       Aptonline   
16336              Northcorp Software   
16817              Kommineni Infotech   
17291   MicroSpark Software Solutions   
17312   MicroSpark Software Solutions   
17826               Kanerika Software   
18082                Vritti Solutions   
18312           Wizertech Informatics   
18325           Wizertech Informatics   
18392             Indovision Services   
18531                IKF Technologies   
18577            QwikCilver Solutions   
18893            Infocus Technologies   
18896        Secure Network Solutions   
18902              AFour Technologies   
19075      Heureux Software Solutions   
19214       Vengai Software Solutions   
19268             Srijan Technologies   
19287             Srijan Technologies   
19372            Ilensys Technologies   

                                       location marketCap sharePrice  \
10123  Hyderabad/Secunderabad, Telangana, India       NaN        NaN   
10172     Bangalore/Bengaluru, Karnataka, India       NaN        NaN   
10331                   Delhi/NCR, Delhi, India       NaN        NaN   
10592                               Pune, India       NaN        NaN   
10843          Gurgaon/Gurugram, Haryana, India       NaN        NaN   
11220  Hyderabad/Secunderabad, Telangana, India       NaN        NaN   
11322                          New Delhi, India       NaN        NaN   
11344                               Pune, India       NaN        NaN   
11556     Bangalore/Bengaluru, Karnataka, India       NaN        NaN   
11568  Hyderabad/Secunderabad, Telangana, India       NaN        NaN   
11811                               Pune, India       NaN        NaN   
11962                Chennai, Tamil Nadu, India       NaN        NaN   
12039                Bangalore,Karnataka, India       NaN        NaN   
12893               Noida, Uttar Pradesh, India       NaN        NaN   
12896                          Hyderabad, India       NaN        NaN   
13035                   Delhi/NCR, Delhi, India       NaN        NaN   
13167                Bangalore,Karnataka, India       NaN        NaN   
14080               Noida, Uttar Pradesh, India       NaN        NaN   
14095               Noida, Uttar Pradesh, India       NaN        NaN   
14113               Noida, Uttar Pradesh, India       NaN        NaN   
14391               Noida, Uttar Pradesh, India       NaN        NaN   
14536               Noida, Uttar Pradesh, India       NaN        NaN   
14681                  Pune, Maharashtra, India       NaN        NaN   
14713                  Pune, Maharashtra, India       NaN        NaN   
14838               Delhi/NCR, New Delhi, India       NaN        NaN   
16077                          Hyderabad, India       NaN        NaN   
16336          Gurgaon/Gurugram, Haryana, India       NaN        NaN   
16817                          Hyderabad, India       NaN        NaN   
17291                          Hyderabad, India       NaN 

In [36]:
result = pd.merge(cluster5, cluster5, on='cluster', suffixes=('_left', '_right'))
result


name_left                             location_left  \
0                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
1                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
2                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
3                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
4                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
...                    ...                                       ...   
2020  Ilensys Technologies                          Hyderabad, India   
2021  Ilensys Technologies                          Hyderabad, India   
2022  Ilensys Technologies                          Hyderabad, India   
2023  Ilensys Technologies                          Hyderabad, India   
2024  Ilensys Technologies                          Hyderabad, India   

     marketCap_left sharePrice_left             category_left  \
0               NaN             NaN  IT Services & Consulting   
1               NaN             NaN  IT Services & Consulting   
2               NaN             NaN  IT Services & Consulting   
3               NaN             NaN  IT Services & Consulting   
4               NaN             NaN  IT Services & Consulting   
...             ...             ...                       ...   
2020            NaN             NaN  IT Services & Consulting   
2021            NaN             NaN  IT Services & Consulting   
2022            NaN             NaN  IT Services & Consulting   
2023            NaN             NaN  IT Services & Consulting   
2024            NaN             NaN  IT Services & Consulting   

     foundationYear_left  cluster                      name_right  \
0                  1997         5                       ValueLabs   
1                  1997         5                      Tata Elxsi   
2                  1997         5      Sysnet Global Technologies   
3                  1997         5  Barclays Global Service Centre   
4                  1997         5  SoftAge Information Technology   
...                  ...      ...                             ...   
2020               2009         5      Heureux Software Solutions   
2021               2009         5       Vengai Software Solutions   
2022               2009         5             Srijan Technologies   
2023               2009         5             Srijan Technologies   
2024               2009         5            Ilensys Technologies   

                                location_right marketCap_right  \
0     Hyderabad/Secunderabad, Telangana, India             NaN   
1        Bangalore/Bengaluru, Karnataka, India             NaN   
2                      Delhi/NCR, Delhi, India             NaN   
3                                  Pune, India             NaN   
4             Gurgaon/Gurugram, Haryana, India             NaN   
...                                        ...             ...   
2020                   Delhi/NCR, Delhi, India             NaN   
2021                          Hyderabad, India             NaN   
2022                   Delhi/NCR, Delhi, India             NaN   
2023                   Delhi/NCR, Delhi, India             NaN   
2024                          Hyderabad, India             NaN   

     sharePrice_right            category_right foundationYear_right  
0                 NaN  IT Services & Consulting                1997   
1                 NaN  IT Services & Consulting                1989   
2                 NaN  IT Services & Consulting                1999   
3                 NaN  IT Services & Consulting                2007   
4                 NaN  IT Services & Consulting                1994   
...               ...                       ...                  ...  
2020              NaN  IT Services & Consulting                2015   
2021              NaN  IT Services & Consulting                2010   
2022              NaN  IT Services & Consulting                2002   
2023              NaN  IT Services & Co